In [15]:
files_year = 2025

In [16]:
import os
import json

directory = './files/'
os.makedirs(directory, exist_ok=True)

In [17]:
months = {
    "janvier": "01", "février": "02", "mars": "03", "avril": "04", "mai": "05", "juin": "06",
    "juillet": "07", "août": "08", "septembre": "09", "octobre": "10", "novembre": "11", "décembre": "12"
}

In [18]:
hijri_months = {
    "mouharram": "01", "safar": "02", "rabî’ al-awwal": "03", "rabî’ ath-thânî": "04",
    "joumada al-oula": "05", "joumada ath-thâniya": "06", "rajab": "07", "chaâbane": "08",
    "ramadhan": "09", "chawwal": "10", "dhou al-qi`da": "11", "dhou al-hijja": "12"
}

In [19]:
defined_titles = ['DECRETS', 'DECISIONS INDIVIDUELLES', 'ARRETES, DECISIONS ET AVIS']

In [20]:
data_file_path = f'./files/{str(files_year)}/data.json'

In [21]:
def init_file(): 
    if not os.path.exists(data_file_path):
        with open(data_file_path, 'w') as f:
            json.dump([], f)

def append_to_json_file(nex_data):
    init_file()
    with open(data_file_path, 'r') as f:
        existing_data = json.load(f)
    existing_data.append(nex_data)
    with open(data_file_path, 'w') as f:
        json.dump(existing_data, f, indent=2)
    

### web scraping (get pdf files)

In [22]:
import requests
from bs4 import BeautifulSoup
import re

links = []

def get_pdfs(year):
    url = f"https://www.joradp.dz/JRN/ZF{year}.htm"
    headers = {"User-Agent": "Mozilla/5.0"}

    response = requests.get(url, headers=headers, verify=False)
    soup = BeautifulSoup(response.text, 'html.parser')

    pdf_links = soup.find_all('a', href=re.compile(r"MaxWin\('(\d+)'\)"))

    for link in pdf_links:
        html_tag = str(link)
        match = re.search(r"MaxWin\('(\d+)'\)", html_tag)
        if match:
            value = match.group(1)
            links.append(f"https://www.joradp.dz/FTP/JO-FRANCAIS/{year}/F{year}{value}.pdf")

In [23]:
get_pdfs(files_year)

/home/mina/anaconda3/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.joradp.dz'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


In [24]:
links

['https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025001.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025002.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025003.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025004.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025005.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025006.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025007.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025008.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025009.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025010.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025011.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025012.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025013.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025014.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025015.pdf',
 'https://www.joradp.dz/FTP/JO-FRANCAIS/2025/F2025018.pdf']

## download pdfs

In [25]:
os.makedirs('./files/' + str(files_year), exist_ok=True)

In [26]:
from pathlib import Path

files = []

for link in links:
    response = requests.get(link)
    files.append(f'./files/{str(files_year)}/{link.split('/')[-1]}')

    file_name = Path(f'./files/{str(files_year)}/{link.split('/')[-1]}')
    file_name.write_bytes(response.content)

In [27]:
files[0]

'./files/2025/F2025001.pdf'

In [28]:
from pdf2image import convert_from_path
import pytesseract
from PIL import Image

# all_data = []

for pdf_file in files:
    images = convert_from_path(pdf_file, dpi=300) 

    print(pdf_file)
    # all_data.append({
    #     'image': '',
    #     'content': []
    # })
    tmp_data = {
        'image': '',
        'content': []
    }
    for i, img in enumerate(images):
        text = pytesseract.image_to_string(img, lang="fra")
        tmp_data['image'] = i
        tmp_data['content'].append(text)
    append_to_json_file(tmp_data)

    

# pdf_path = "./files/2025/F2025014.pdf"
# images = convert_from_path(pdf_path, dpi=300) 



# for i, img in enumerate(images):
#     all_data.append({
#         'image': images[i],
#         'content': []
#     })
#     print("#"*20)
#     print(i + 1)
#     print(f"Page {i+1}\n")
#     text = pytesseract.image_to_string(img, lang="fra")
#     text = '\n\n'.join(text)
#     all_data[-1]['content'].append(text)

./files/2025/F2025001.pdf
./files/2025/F2025002.pdf
./files/2025/F2025003.pdf
./files/2025/F2025004.pdf
./files/2025/F2025005.pdf
./files/2025/F2025006.pdf
./files/2025/F2025007.pdf
./files/2025/F2025008.pdf
./files/2025/F2025009.pdf
./files/2025/F2025010.pdf
./files/2025/F2025011.pdf
./files/2025/F2025012.pdf
./files/2025/F2025013.pdf
./files/2025/F2025014.pdf
./files/2025/F2025015.pdf
./files/2025/F2025018.pdf


In [29]:
all_data

NameError: name 'all_data' is not defined

In [30]:
import json
import os

def read_json_file():
    if not os.path.exists(data_file_path):
        return []
    with open(data_file_path, 'r') as f:
        return json.load(f)


all_data = read_json_file()
all_data
# json_obj = json.dumps(all_data)

# with open(f'./files/{str(files_year)}/data.json', 'w') as f:
#     f.write(json.dumps(all_data))

[{'image': 19,
  'content': ["N° 01 Mardi 7 Rajab 1446\n\n64ème ANNEE Correspondant au 7 janvier 2025\n\nF3 15 H 6G\nSEM 5 SMl e p Hila 6 Ghyzhe celjls GHI\n\nJOURNAL OH FICIRL\n\nDI [LA IRIEPUBLIQUIE ALCGERTENNE DIEMOCRATIQUIE ET POIPULANURE\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n(TRADUCTION FRANÇAISE)\n\nAlgérie ETRANGER DIRECTION ET REDACTION\n\nTunisie\nSECRETARIAT GENERAL\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\n\nANNUEL Libye que le Maghreb)\nMauritanie Abonnement et publicié :\n\nIMPRIMFRIE OFFICIELLE\n\nLes Vergers, Bir Mourad Raïs, BP 376\nALGER-GARE\n\nEdition originale 1090,00 D.A 2675,00 D.A Tél : 023 41.18.89 à 92\nFax : 023.41.18.76\nEdition originale et sa traductionT…| 2180,00 D.A 5350,00 D.A C.C.P. 3200-50 Clé 68 Alger\nBADR : Rib 00 300 060000201930048\nETRANGER : (Compte devises)\nBADR : 003 00 060000014720242\n\n(Frais d’expédition en sus)\n\nEdition originale, le numéro : 14,00 dinars. 

In [ ]:
# file = open("output.txt", "r").read()
# file

In [ ]:
import json
import pandas as pd

result = []

In [ ]:
all_data[0]['content']

["N° 01 Mardi 7 Rajab 1446\n\n64ème ANNEE Correspondant au 7 janvier 2025\n\nF3 15 H 6G\nSEM 5 SMl e p Hila 6 Ghyzhe celjls GHI\n\nJOURNAL OH FICIRL\n\nDI [LA IRIEPUBLIQUIE ALCGERTENNE DIEMOCRATIQUIE ET POIPULANURE\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n(TRADUCTION FRANÇAISE)\n\nAlgérie ETRANGER DIRECTION ET REDACTION\n\nTunisie\nSECRETARIAT GENERAL\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\n\nANNUEL Libye que le Maghreb)\nMauritanie Abonnement et publicié :\n\nIMPRIMFRIE OFFICIELLE\n\nLes Vergers, Bir Mourad Raïs, BP 376\nALGER-GARE\n\nEdition originale 1090,00 D.A 2675,00 D.A Tél : 023 41.18.89 à 92\nFax : 023.41.18.76\nEdition originale et sa traductionT…| 2180,00 D.A 5350,00 D.A C.C.P. 3200-50 Clé 68 Alger\nBADR : Rib 00 300 060000201930048\nETRANGER : (Compte devises)\nBADR : 003 00 060000014720242\n\n(Frais d’expédition en sus)\n\nEdition originale, le numéro : 14,00 dinars. Edition originale et sa trad

In [31]:
def extract_data(all_data):
    for content in all_data:
        file = content['content']

        file = '\n\n'.join(file)
        
        # start metadata
        metadata = file.split('SOMMAIRE')[0]

        # get source
        source_match = re.search(r"N°\s*(\d+)", metadata.split('\n\n')[0])
        source_match = source_match.group(1) if source_match else None

        # get hijri date
        hijri_match = re.search(r"(\d+)\s+([a-zâû]+)\s+(\d{4})", metadata.split('\n\n')[0], re.IGNORECASE)
        if hijri_match:
            hijri_day, hijri_month, hijri_year = hijri_match.groups()
            
            hijri_month_num = hijri_months.get(hijri_month.lower(), '00')  # Keep original name if not found
            hijri_date = f"{hijri_day} {hijri_month} {hijri_year}"
        else:
            hijri_date = None
        
        # get date
        date_match = re.search(r"(\d+)\s+([a-zéû]+)\s+(\d{4})", metadata.split('\n\n')[1], re.IGNORECASE)
        if date_match:
            day, month, year = date_match.groups()
            date = f"{day} {month} {year}" 
        else:
            date = None

        # start extracting content
        data = {}
        data['metadata'] = {
            "journal_number": source_match,
            "hijri_date": hijri_date,
            "gregorian_date": date
        }
        data['types'] = []

        file = file.split('SOMMAIRE')[1: ]
        file = 'SOMMAIRE '.join(file)
        file = file.split('\n\n')

        df = pd.DataFrame(file)

        titles = [col for col in df[0] if col.isupper()]
        titles = [col for col in titles if not any(char.isdigit() for char in col)]
        titles = [col for col in titles if "OFFICIELLE" or 'JOURNAL' not in col]

        first_title = titles[0]

        column_index = [i for i, col in enumerate(df[0]) if col == first_title]

        sommaire = df[: column_index[-1]]
        sommaire = sommaire[~sommaire.applymap(lambda x: any(char.isdigit() for char in str(x)) or any(char.islower() for char in str(x))).any(axis=1)]
        sommaire.drop(sommaire[sommaire[0] == ''].index, inplace=True)

        for i, title in enumerate(sommaire[0]):
            if title != '' and not title.startswith('MINISTERE'):
                data['types'].append({
                    'type_name': title,
                    'ministries': []
                })
            elif title != '' and title.startswith('MINISTERE'):
                data['types'][-1]['ministries'].append({
                    'ministry_name': title,
                    'decrets': []
                })
        
        for data_type in data['types']: 
            if data_type['ministries'] == []:
                data_type['ministries'].append({
                    'ministry_name': '',
                    'decrets': []
                })
        
        df = df[column_index[-1]: ]

        df = df[~df.applymap(lambda x: x == '').all(axis=1)]
        df = df[~df.applymap(lambda x: 'Le Premier ministre,' == str(x)).any(axis=1)]
        df = df[~df.applymap(lambda x: 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in str(x)).any(axis=1)]
        df = df[~df.applymap(lambda x: 'Décrète :' == str(x)).any(axis=1)]
        df = df[~df.applymap(lambda x: 'Arrête :' == str(x)).any(axis=1)]
        df = df[~df.applymap(lambda x: str(x).startswith('Sur le rapport du ministre')).any(axis=1)]
        df = df[~df.applymap(lambda x: 'x' == str(x)).any(axis=1)]

        file = ' '.join(file)

        current_type = None
        decret_pattern = re.compile(r"^(?:Décret exécutif n°\s*\d+.*|Décret présidentiel du\s*\d+.*|Arrêté du\s*\d+.*)$", re.IGNORECASE | re.MULTILINE)
        article_pattern = re.compile(r"^(?:Article|Art\.)\s+\d*|l\.", re.IGNORECASE | re.MULTILINE)
        citation_pattern = re.compile(r"^Vu\s+.*$", re.IGNORECASE | re.MULTILINE)

        current_decret = ''
        current_articles = []
        current_citations = []
        others = ''

        for index, row in df.iterrows():
            text = row[0].strip().split('\n')
            text = ' '.join(text)
            text = re.sub(r" {2,}", " ", text)
            text = re.sub(r"^[^\w]+|[^\w]+$", "", text)
        
            for entry in data["types"]:
                if text == entry["type_name"]:
                    current_type = entry  
                    break
        
            if current_type and text not in [t["type_name"] for t in data["types"]]:
                ministry = current_type["ministries"][0] 
                
                for min_entry in current_type["ministries"]:
                    if min_entry["ministry_name"] and min_entry["ministry_name"] == text:
                        ministry = min_entry
                        current_decret = ''
                        break
                
                if decret_pattern.match(text):
                    if current_decret:
                        for structure in ministry["decrets"]:
                            if structure["decret_title"] == current_decret:
                                structure["articles"] = current_articles
                                structure["citations"] = current_citations
                                structure["others"] = others
                                break
            
                    current_decret = text
                    current_articles = []
                    current_citations = []
                    others = ''
                
                elif article_pattern.match(text):
                    words = text.strip().split()
                    if words[0] in ['Article', 'Art.']:
                        number = words[1].replace("er.", "").replace(".", "").replace("—", "").replace("&", "")
                        words = words[2:]
                        words = ' '.join(words)
                    current_articles.append({
                        "article_title": 'Article ' + number,
                        "article_content": words
                    })
            
                elif current_articles:
                    current_articles[-1]["article_content"] += " " + text
            
                elif citation_pattern.match(text):
                    current_citations.append(text)
                else:
                    others += text
        
                if not ministry["decrets"] or not any(dec['decret_title'] == current_decret for dec in ministry["decrets"]):
                    ministry["decrets"].append({
                        'decret_title': current_decret,
                        "articles": current_articles,
                        "citations": current_citations,
                        'others': others
                    })
        result.append(data)

In [34]:
import pandas as pd
result = []

extract_data(all_data)

/tmp/ipykernel_56997/3620391509.py:56: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  sommaire = sommaire[~sommaire.applymap(lambda x: any(char.isdigit() for char in str(x)) or any(char.islower() for char in str(x))).any(axis=1)]
/tmp/ipykernel_56997/3620391509.py:80: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: x == '').all(axis=1)]
/tmp/ipykernel_56997/3620391509.py:81: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'Le Premier ministre,' == str(x)).any(axis=1)]
/tmp/ipykernel_56997/3620391509.py:82: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in str(x)).any(axis=1)]
/tmp/ipykernel_56997/3620391509.py:83: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applyma

IndexError: list index out of range

In [35]:
result

[{'metadata': {'journal_number': '01',
   'hijri_date': '7 Rajab 1446',
   'gregorian_date': '7 janvier 2025'},
  'types': [{'type_name': 'DECISIONS INDIVIDUELLES',
    'ministries': [{'ministry_name': '',
      'decrets': [{'decret_title': 'Décret présidentiel du 7 Rajab 1446 correspondant au 7 janvier 2025 mettant fin aux fonctions d’un chargé d’études et de synthèse au rectorat de Djamaâ Fl Djazaïr',
        'articles': [],
        'citations': [],
        'others': 'Par décret présidentiel du 7 Rajab 1446 correspondant au 7 janvier 2025, il est mis fin au fonctions de chargé d’études et de synthèse au rectorat de DjamaÂ El Djazaïr, exercées par M. Tahar Braik, appelé à exercer une autre fonction. x'},
       {'decret_title': 'Décret présidentiel du 7 Rajab 1446 correspondant au 7 janvier 2025 portant nomination du directeur général de l’office national du pélerinage et de la omra (ONPO',
        'articles': [{'article_title': 'Article l',
          'article_content': "— En applicat

In [36]:
print(json.dumps(result, indent=4, ensure_ascii=False))

[
    {
        "metadata": {
            "journal_number": "01",
            "hijri_date": "7 Rajab 1446",
            "gregorian_date": "7 janvier 2025"
        },
        "types": [
            {
                "type_name": "DECISIONS INDIVIDUELLES",
                "ministries": [
                    {
                        "ministry_name": "",
                        "decrets": [
                            {
                                "decret_title": "Décret présidentiel du 7 Rajab 1446 correspondant au 7 janvier 2025 mettant fin aux fonctions d’un chargé d’études et de synthèse au rectorat de Djamaâ Fl Djazaïr",
                                "articles": [],
                                "citations": [],
                                "others": "Par décret présidentiel du 7 Rajab 1446 correspondant au 7 janvier 2025, il est mis fin au fonctions de chargé d’études et de synthèse au rectorat de DjamaÂ El Djazaïr, exercées par M. Tahar Braik, appelé à exercer une autre 

In [ ]:
# save all_data variable in a json file
import json
with open(f'./files/{str(files_year)}/result.json', 'w') as f:
    json.dump(result, f)

In [ ]:
file = all_data[1]['content']

file = '\n\n'.join(file)
file

'N° 02 Jeudi 9 Rajab 1446\n\n64ème ANNEE / \\ e BT Correspondant au 9 janvier 2025\n\n?ÎÏ’/’ ‘ L/"Ï ‘ :_\'_JU 0bl!\nÔÉMÿ_,&L."N\\_&A_Â;L«H übj““l)\')&\\)\\;’\n\nJOURNAL OFFICTRL\n\nDI ILA RE PUBLIQUE ALGERDENNE DEMOCRATIQUIE E POPULAURE\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n(TRADUCTION FRANÇAISE)\n\nAlgérie ETRANGER DIRECTION ET REDACTION\nTunisie SECRETARIAT GENERAL\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\n\nANNUEL Libye que le Maghreb) WWW.JORADP.DZ\nMauritanie Abonnement et publicité:\nIMPRIMERIE OFFICIELLE\n\nLes Vergers, Bir-Mourad Raïs, BP 376\nALGER-GARE\n\nEdition originale 1090,00 D.A 2675,00 D.A Tél : 023.41.18.89 à 92\nFax : 023.41.18.76\nEdition originale et sa traduction 2180.00 D.A 5350,00 D.A C.C.P. 3200-50 Clé 68 ALGER\n) BADR : Rib 00 300 060000201930048\nETRANGER : (Compte devises)\nBADR : 003 00 060000014720242\n\n(Frais d\'expédition en sus\n\nEdition originale, le numéro : 14,00 dinars

In [ ]:
metadata = file.split('SOMMAIRE')[0]
metadata

'N° 02 Jeudi 9 Rajab 1446\n\n64ème ANNEE / \\ e BT Correspondant au 9 janvier 2025\n\n?ÎÏ’/’ ‘ L/"Ï ‘ :_\'_JU 0bl!\nÔÉMÿ_,&L."N\\_&A_Â;L«H übj““l)\')&\\)\\;’\n\nJOURNAL OFFICTRL\n\nDI ILA RE PUBLIQUE ALGERDENNE DEMOCRATIQUIE E POPULAURE\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n(TRADUCTION FRANÇAISE)\n\nAlgérie ETRANGER DIRECTION ET REDACTION\nTunisie SECRETARIAT GENERAL\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\n\nANNUEL Libye que le Maghreb) WWW.JORADP.DZ\nMauritanie Abonnement et publicité:\nIMPRIMERIE OFFICIELLE\n\nLes Vergers, Bir-Mourad Raïs, BP 376\nALGER-GARE\n\nEdition originale 1090,00 D.A 2675,00 D.A Tél : 023.41.18.89 à 92\nFax : 023.41.18.76\nEdition originale et sa traduction 2180.00 D.A 5350,00 D.A C.C.P. 3200-50 Clé 68 ALGER\n) BADR : Rib 00 300 060000201930048\nETRANGER : (Compte devises)\nBADR : 003 00 060000014720242\n\n(Frais d\'expédition en sus\n\nEdition originale, le numéro : 14,00 dinars

In [ ]:
source_match = re.search(r"N°\s*(\d+)", metadata.split('\n\n')[0])
source_match = source_match.group(1) if source_match else None
source_match

'02'

In [ ]:
hijri_match = re.search(r"(\d+)\s+([a-zâû]+)\s+(\d{4})", metadata.split('\n\n')[0], re.IGNORECASE)
if hijri_match:
    hijri_day, hijri_month, hijri_year = hijri_match.groups()
    
    hijri_month_num = hijri_months.get(hijri_month.lower(), '00')  # Keep original name if not found
    hijri_date = f"{hijri_day} {hijri_month} {hijri_year}"
else:
    hijri_date = None

hijri_date

'9 Rajab 1446'

In [ ]:
date_match = re.search(r"(\d+)\s+([a-zéû]+)\s+(\d{4})", metadata.split('\n\n')[1], re.IGNORECASE)

if date_match:
    day, month, year = date_match.groups()
    date = f"{day} {month} {year}" 
else:
    date = None

print(date)

9 janvier 2025


In [ ]:
import json

data = {}

data['metadata'] = {
    "journal_number": source_match,
    "hijri_date": hijri_date,
    "gregorian_date": date
}
data['types'] = []


data

{'metadata': {'journal_number': '02',
  'hijri_date': '9 Rajab 1446',
  'gregorian_date': '9 janvier 2025'},
 'types': []}

In [ ]:
file

'N° 02 Jeudi 9 Rajab 1446\n\n64ème ANNEE / \\ e BT Correspondant au 9 janvier 2025\n\n?ÎÏ’/’ ‘ L/"Ï ‘ :_\'_JU 0bl!\nÔÉMÿ_,&L."N\\_&A_Â;L«H übj““l)\')&\\)\\;’\n\nJOURNAL OFFICTRL\n\nDI ILA RE PUBLIQUE ALGERDENNE DEMOCRATIQUIE E POPULAURE\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n(TRADUCTION FRANÇAISE)\n\nAlgérie ETRANGER DIRECTION ET REDACTION\nTunisie SECRETARIAT GENERAL\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\n\nANNUEL Libye que le Maghreb) WWW.JORADP.DZ\nMauritanie Abonnement et publicité:\nIMPRIMERIE OFFICIELLE\n\nLes Vergers, Bir-Mourad Raïs, BP 376\nALGER-GARE\n\nEdition originale 1090,00 D.A 2675,00 D.A Tél : 023.41.18.89 à 92\nFax : 023.41.18.76\nEdition originale et sa traduction 2180.00 D.A 5350,00 D.A C.C.P. 3200-50 Clé 68 ALGER\n) BADR : Rib 00 300 060000201930048\nETRANGER : (Compte devises)\nBADR : 003 00 060000014720242\n\n(Frais d\'expédition en sus\n\nEdition originale, le numéro : 14,00 dinars

In [ ]:
file = file.split('SOMMAIRE')[1: ]
file = 'SOMMAIRE '.join(file)
file

'\n\nDécret présidentiel n° 25-04 du 9 Rajab 1446 correspondant au 9 janvier 2025 portant répartition des autorisations d’engagement et\ndes crédits de paiement ouverts, au titre du budget de l’Etat, par la loi de finances pour 2025, mis à la disposition de la\n\nPrésidence de la République\n\nDécret présidentiel n° 25-05 du 9 Rajab 1446 correspondant au 9 janvier 2025 portant répartition des autorisations d’engagement et\ndes crédits de paiement ouverts, au titre du budget de l’Etat, par la loi de finances pour 2025, mis à la disposition du ministre\n\nd’Etat, ministre des affaires étrangères, de la communauté nationale à l’étranger et des affaires africaines\n\nDécret présidentiel n° 25-06 du 9 Rajab 1446 correspondant au 9 janvier 2025 portant répartition des autorisations d’engagement et\ndes crédits de paiement ouverts, au titre du budget de l’Etat, par la loi de finances pour 2025, mis à la disposition du Président\n\ndu Conseil de la Nation\n\nDécret présidentiel n° 25-07 du 9 R

In [ ]:
import pandas as pd

file = file.split('\n\n')
df = pd.DataFrame(file)
df

AttributeError: 'list' object has no attribute 'split'

In [ ]:
titles = [col for col in df[0] if col.isupper()]
titles

['JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 02',
 'JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 02',
 'JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 02',
 'DECRETS',
 'JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 02',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 '3 000 000 3 000 000 I 63000 000 000 | 63000 000 000 | 63003000 000 | 63003 000 000',
 'JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 02',
 'ETAT ANNEXE',
 'R\nL\n620 000 000 000 | 620 000 000 000 | 620 696 272.000 | 620 696 272.000\n500 000 000 000 | 500 000 000 000 | 500 015 000 000 | 500 015 000 000\n" 120 000 000 000 Ë 120 681 272000 | 120 681 272000',
 '10 528 300 000 |15 963 800 000 | 27 788 211 000 | 27 788 211 000 | 103919 011 000 | 109 354 SI1 000\n9288 300 000 |13 144 800 000 | 27 788 211 000 |27 788 211 000 | 101 691 511 000 | 105548 011 000',
 'ETAT ANNEXE',
 '3 600 000 000 ÊËÊ 230 000 000\n10 000 000'

In [ ]:

# remove column if it does contain numbers
titles = [col for col in titles if not any(char.isdigit() for char in col)]

# remove column if it contains "JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE"
titles = [col for col in titles if "OFFICIELLE" or 'JOURNAL' not in col]
titles

['DECRETS',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 '" L',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'N',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 "- E\n' S",
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'ETAT ANNEXE',
 'GARE']

In [ ]:
first_title = titles[0]
first_title

'DECRETS'

In [ ]:
column_index = [i for i, col in enumerate(df[0]) if col == first_title]
column_index[-1]

104

In [ ]:
sommaire = df[: column_index[-1]]
sommaire

0
0                                                     
1    Décret présidentiel n° 25-04 du 9 Rajab 1446 c...
2                          Présidence de la République
3    Décret présidentiel n° 25-05 du 9 Rajab 1446 c...
4    d’Etat, ministre des affaires étrangères, de l...
..                                                 ...
99   Décret exécutif n° 25-51 du 9 Rajab 1446 corre...
100  Décret exécutif n° 25-52 du 9 Rajab 1446 corre...
101                                                   
102                                       9 Rajab 1446
103  JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...

[104 rows x 1 columns]

In [ ]:
sommaire = sommaire[~sommaire.applymap(lambda x: any(char.isdigit() for char in str(x))).any(axis=1)]
sommaire = sommaire[~sommaire.applymap(lambda x: any(any(char.islower() for char in str(x)))).any(axis=1)]
sommaire.drop(sommaire[sommaire[0] == ''].index, inplace=True)
sommaire

/tmp/ipykernel_46267/3528636105.py:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  sommaire = sommaire[~sommaire.applymap(lambda x: any(char.isdigit() for char in str(x))).any(axis=1)]
/tmp/ipykernel_46267/3528636105.py:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  sommaire = sommaire[~sommaire.applymap(lambda x: any(any(char.islower() for char in str(x)))).any(axis=1)]


TypeError: 'bool' object is not iterable

In [ ]:
sommaire[0]

0                                                       
2                            Présidence de la République
4      d’Etat, ministre des affaires étrangères, de l...
6                                du Conseil de la Nation
8                     de l’Assemblée Populaire Nationale
10                          de la Cour constitutionnelle
15               du Conseil Supérieur de la Magistrature
19     d’Etat, ministre de l'énergie, des mines et de...
21     l’intérieur, des collectivités locales et de l...
23                             justice, garde des sceaux
24                                                      
27                                     SOMMAIRE  (suite)
29                                              finances
31                      moudjahidine et des ayants droit
33                     affaires religieuses et des wakfs
35     l'enseignement supérieur et de la recherche sc...
37                                 l’éducation nationale
39         formation et de l’en

In [ ]:
data

{'metadata': {'journal_number': '02',
  'hijri_date': '9 Rajab 1446',
  'gregorian_date': '9 janvier 2025'},
 'types': []}

In [ ]:
for i, title in enumerate(sommaire[0]):
    if title != '' and not title.startswith('MINISTERE'):
        data['types'].append({
            'type_name': title,
            'ministries': []
        })
    elif title != '' and title.startswith('MINISTERE'):
        data['types'][-1]['ministries'].append({
            'ministry_name': title,
            'decrets': []
        })

In [ ]:
data

{'metadata': {'journal_number': '02',
  'hijri_date': '9 Rajab 1446',
  'gregorian_date': '9 janvier 2025'},
 'types': [{'type_name': 'Présidence de la République', 'ministries': []},
  {'type_name': 'd’Etat, ministre des affaires étrangères, de la communauté nationale à l’étranger et des affaires africaines',
   'ministries': []},
  {'type_name': 'du Conseil de la Nation', 'ministries': []},
  {'type_name': 'de l’Assemblée Populaire Nationale', 'ministries': []},
  {'type_name': 'de la Cour constitutionnelle', 'ministries': []},
  {'type_name': 'du Conseil Supérieur de la Magistrature', 'ministries': []},
  {'type_name': "d’Etat, ministre de l'énergie, des mines et des énergies renouvelables",
   'ministries': []},
  {'type_name': 'l’intérieur, des collectivités locales et de l’aménagement du territoire',
   'ministries': []},
  {'type_name': 'justice, garde des sceaux', 'ministries': []},
  {'type_name': 'SOMMAIRE  (suite)', 'ministries': []},
  {'type_name': 'finances', 'ministries'

In [ ]:
for data_type in data['types']: 
    if data_type['ministries'] == []:
        print(data_type)
        data_type['ministries'].append({
            'ministry_name': '',
            'decrets': []
        })

{'type_name': 'DECRETS', 'ministries': []}
{'type_name': 'DECISIONS INDIVIDUELLES', 'ministries': []}


In [ ]:
data

{'metadata': {'journal_number': '13',
  'hijri_date': '26 Chaâbane 1446',
  'gregorian_date': '25 février 2025'},
 'types': [{'type_name': 'DECRETS',
   'ministries': [{'ministry_name': '', 'decrets': []}]},
  {'type_name': 'DECISIONS INDIVIDUELLES',
   'ministries': [{'ministry_name': '', 'decrets': []}]},
  {'type_name': 'ARRETES, DECISIONS ET AVIS',
   'ministries': [{'ministry_name': "MINISTERE DU TOURISME ET DE L'ARTISANAT",
     'decrets': []},
    {'ministry_name': "MINISTERE DE L'INDUSTRIE PHARMACEUTIQUE",
     'decrets': []}]}]}

In [ ]:
df = df[column_index[-1]: ]

In [ ]:
df

0
26                                             DECRETS
27   Décret exécutif n° 25-84 du 21 Chaâbane 1446\n...
28                                Le Premier ministre,
29   Sur le rapport du ministre d’Etat, ministre de...
30   Vu la Constitution, notamment ses articles 112...
..                                                 ...
884  Article 1er. — Les dispositifs médicaux fabriq...
885  Art. 2. — Le présent arrêté sera publié au Jou...
886  Fait à Alger, le 21 Chaâbane 1446 correspondan...
887                                    Ouacim KOUIDRI.
888  Imprimerie Officielle - Les Vergers, Bir-Moura...

[863 rows x 1 columns]

In [ ]:
# remove rows that contain only empty strings
df = df[~df.applymap(lambda x: x == '').all(axis=1)]

# remove row if row = "Le Premier ministre"
df = df[~df.applymap(lambda x: 'Le Premier ministre,' == str(x)).any(axis=1)]
df = df[~df.applymap(lambda x: 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in str(x)).any(axis=1)]
df = df[~df.applymap(lambda x: 'Décrète :' == str(x)).any(axis=1)]
df = df[~df.applymap(lambda x: 'Arrête :' == str(x)).any(axis=1)]
df = df[~df.applymap(lambda x: str(x).startswith('Sur le rapport du ministre')).any(axis=1)]
df = df[~df.applymap(lambda x: 'x' == str(x)).any(axis=1)]

/tmp/ipykernel_29469/1745186790.py:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: x == '').all(axis=1)]
/tmp/ipykernel_29469/1745186790.py:5: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'Le Premier ministre,' == str(x)).any(axis=1)]
/tmp/ipykernel_29469/1745186790.py:6: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in str(x)).any(axis=1)]
/tmp/ipykernel_29469/1745186790.py:7: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'Décrète :' == str(x)).any(axis=1)]
/tmp/ipykernel_29469/1745186790.py:8: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df[~df.applymap(lambda x: 'Arrête :' == str(x)).any(axis=1)]
/tmp/ipykernel_29469/1745186790.py:

In [ ]:
df

0
26                                             DECRETS
27   Décret exécutif n° 25-84 du 21 Chaâbane 1446\n...
30   Vu la Constitution, notamment ses articles 112...
31   Vu le décret présidentiel n° 23-404 du 27 Rabi...
32   Vu le décret présidentiel n° 24-374 du 16 Joum...
..                                                 ...
884  Article 1er. — Les dispositifs médicaux fabriq...
885  Art. 2. — Le présent arrêté sera publié au Jou...
886  Fait à Alger, le 21 Chaâbane 1446 correspondan...
887                                    Ouacim KOUIDRI.
888  Imprimerie Officielle - Les Vergers, Bir-Moura...

[806 rows x 1 columns]

In [ ]:
file = ' '.join(file)
file

" DECRETS Décret exécutif n° 25-84 du 21 Chaâbane 1446 correspondant au 20 février 2025 fixant les attributions du ministre de l'énergie, des\nmines et des énergies renouvelables Décret exécutif n° 25-85 du 21 Chaâbane 1446 correspondant au 20 février 2025 portant organisation de l'administration centrale du\nministère de l'énergie, des mines et des énergies renouvelables Décret exécutif n° 25-86 du 23 Chaâbane 1446 correspondant au 22 février 2025 instituant une allocation de solidarité spéciale pour\nle mois de Ramadhan DECISIONS INDIVIDUELLES Décret présidentiel du 19 Chaâbane 1446 correspondant au 18 février 2025 mettant fin aux fonctions du directeur général des libertés\npubliques et des affaires juridiques au ministère de l'intérieur, des collectivités locales et de l'aménagement du territoire Décret présidentiel du 19 Chaâbane 1446 correspondant au 18 février 2025 mettant fin aux fonctions du directeur général de la\nmodernisation, de la documentation et des archives au ministè

In [ ]:
current_type = None

decret_pattern = re.compile(r"^(?:Décret exécutif n°\s*\d+.*|Décret présidentiel du\s*\d+.*|Arrêté du\s*\d+.*)$", re.IGNORECASE | re.MULTILINE)

article_pattern = re.compile(r"^(?:Article|Art\.)\s+\d*|l\.", re.IGNORECASE | re.MULTILINE)


In [ ]:
citation_pattern = re.compile(r"^Vu\s+.*$", re.IGNORECASE | re.MULTILINE)

for index, row in df.iterrows():
    text = row[0].strip().split('\n')
    text = ' '.join(text)
    text = re.sub(r" {2,}", " ", text)
    text = re.sub(r"^[^\w]+|[^\w]+$", "", text)

    for entry in data["types"]:
        if text == entry["type_name"]:
            current_type = entry  
            break

    if current_type and text not in [t["type_name"] for t in data["types"]]:
        ministry = current_type["ministries"][0] 
        
        for min_entry in current_type["ministries"]:
            if min_entry["ministry_name"] and min_entry["ministry_name"] == text:
                ministry = min_entry
                current_decret = ''
                break
        
        if decret_pattern.match(text):
            if current_decret:
                for structure in ministry["decrets"]:
                    if structure["decret_title"] == current_decret:
                        structure["articles"] = current_articles
                        structure["citations"] = current_citations
                        structure["others"] = others
                        break
    
            current_decret = text
            current_articles = []
            current_citations = []
            others = ''
        
        elif article_pattern.match(text):
            words = text.strip().split()
            if words[0] in ['Article', 'Art.']:
                number = words[1].replace("er.", "").replace(".", "").replace("—", "").replace("&", "")
                words = words[2:]
                words = ' '.join(words)
            current_articles.append({
                "article_title": 'Article ' + number,
                "article_content": words
            })
    
        elif current_articles:
            current_articles[-1]["article_content"] += " " + text
    
        elif citation_pattern.match(text):
            current_citations.append(text)
        else:
            others += text
            print(others)

        if not ministry["decrets"] or not any(dec['decret_title'] == current_decret for dec in ministry["decrets"]):
            ministry["decrets"].append({
                'decret_title': current_decret,
                "articles": current_articles,
                "citations": current_citations,
                'others': others
            })



1445 correspondant au 11 novembre 2023 portant nomination du Premier ministre
1445 correspondant au 11 novembre 2023 portant nomination du Premier ministreDécrète : Article 1er. — Sous l'autorité du ministre, l'administration
1445 correspondant au 11 novembre 2023 portant nomination du Premier ministreDécrète : Article 1er. — Sous l'autorité du ministre, l'administrationcentrale du ministère de l'énergie, des mines et des énergies renouvelables comprend
1445 correspondant au 11 novembre 2023 portant nomination du Premier ministreDécrète : Article 1er. — Sous l'autorité du ministre, l'administrationcentrale du ministère de l'énergie, des mines et des énergies renouvelables comprend1. Le secrétaire général, assisté de deux (2) directeurs d'études, auquel sont rattachés le bureau du courrier et le bureau ministériel de la sûreté interne d'établissement
1445 correspondant au 11 novembre 2023 portant nomination du Premier ministreDécrète : Article 1er. — Sous l'autorité du ministre, l'admin

In [ ]:
print(json.dumps(data, indent=4, ensure_ascii=False))

{
    "metadata": {
        "journal_number": "13",
        "hijri_date": "26 Chaâbane 1446",
        "gregorian_date": "25 février 2025"
    },
    "types": [
        {
            "type_name": "DECRETS",
            "ministries": [
                {
                    "ministry_name": "",
                    "decrets": [
                        {
                            "decret_title": "Décret exécutif n° 25-84 du 21 Chaâbane 1446 correspondant au 20 février 2025 fixant les attributions du ministre de l'énergie, des mines et des énergies renouvelables",
                            "articles": [
                                {
                                    "article_title": "Article l",
                                    "article_content": "— Dans le cadre de la politique générale du Gouvernement, le ministre de l'énergie, des mines et des énergies renouvelables est chargé de l'élaboration des politiques et des stratégies de recherche, de production et de valorisation des

In [ ]:
print(current_decret)

Arrêté du 21 Chaâbane 1446 correspondant au 20 février 2025 autorisant la commercialisation des dispositifs médicaux
